In [45]:
import hashlib
import time
import ecdsa
import random
import string

### Defines a wallet with a public and private key and balance

In [46]:
class Wallet:
    def __init__(self, name):
        # Generate a random private and public key pair for the wallet using secp256k1 curve
        self.name = name
        self.private_key = ecdsa.SigningKey.generate(curve=ecdsa.SECP256k1).to_string().hex()
        self.public_key = hashlib.sha256(self.private_key.encode()).hexdigest()
        self.balance = 0

    def add_balance(self, amount):
        self.balance += amount
        return self
    
    def display_all_wallet(self):
        print(f"Wallet {self.name}:")
        print(f"  Public Key: {self.public_key}")
        print(f"  Private Key: {self.private_key}")
        print(f"  Balance: {self.balance} units")

    def display_public_key(self):
        print(f"Public Key: {self.public_key}")

    def display_private_key(self):
        print(f"Private Key: {self.private_key}")

### Defines the transaction sender, recipient, amount, time, id

In [47]:
class Transaction:
    def __init__(self, sender, recipient, amount):
        self.sender = sender
        self.recipient = recipient
        self.amount = amount
        self.timestamp = time.time()
        self.transaction_id = self.calculate_transaction_id()

    def calculate_transaction_id(self):
        # Hash the transaction details to create a unique identifier
        data = f"{self.sender.public_key if self.sender else 'None'}{self.recipient.public_key}{self.amount}{self.timestamp}"
        return hashlib.sha256(data.encode()).hexdigest()

    def end_transaction(self):
        if self.sender and self.sender.balance < self.amount:
            raise ValueError("Insufficient funds for the transaction.")

        # Add the amount to the recipient's balance
        self.recipient.balance += self.amount


    def display_transaction(self):
        formatted_timestamp = time.strftime("%m/%d/%Y %H:%M:%S", time.localtime(self.timestamp))
        print("Transaction:")
        print(f"  Sender Public Key: {self.sender.public_key if self.sender else 'None'}")
        print(f"  Recipient Public Key: {self.recipient.public_key}")
        print(f"  Amount: {self.amount}")
        print(f"  Timestamp: {formatted_timestamp}")
        print(f"  Transaction ID: {self.transaction_id}")

### Defines the Block which has a number, timestamp, transaction data, previous hash and its hash

In [48]:
class Block:
    def __init__(self, block_number, previous_hash, transactions):
        self.block_number = block_number
        self.timestamp = time.time()
        self.transactions = transactions
        self.previous_hash = previous_hash
        self.nonce = 0  # Add a nonce attribute
        self.hash = self.calculate_hash()

    def calculate_hash(self):
        data = (
            str(self.block_number)
            + str(self.timestamp)
            + str([transaction.transaction_id for transaction in self.transactions])
            + str(self.previous_hash)
            + str(self.nonce)  # Include the nonce in the hash calculation
        )
        return hashlib.sha256(data.encode()).hexdigest()

### Defines the blockchain Creates the first block when called and then has a function to add_blocks (in a real blockchain the Blockchain.chain would be immutable but in this case it isn't)

In [49]:
class Blockchain:
    def __init__(self):
        self.chain = [self.create_genesis_block()]
        self.current_transactions = []

    def create_genesis_block(self):
        # Create the first block in the chain (Genesis Block)
        return Block(0, "0", [])

    def mine_block(self, miner_wallet, miner_reward, difficulty=4):
        # Create a new block with the pending transactions
        new_block = Block(len(self.chain), self.chain[-1].hash, self.current_transactions)
        # Reset the list of pending transactions
        self.current_transactions = []

        # Simulate proof-of-work
        self.proof_of_work(new_block, difficulty)

        # Reward the miner for mining a new block
        miner_transaction = Transaction(None, miner_wallet, miner_reward)
        miner_transaction.end_transaction()

        # Execute all transactions in the mined block
        for transaction in new_block.transactions:
            transaction.end_transaction()

        # Add the new block to the blockchain
        self.chain.append(new_block)

    def proof_of_work(self, block, difficulty):
        prefix = '0' * difficulty
        nonce = 0

        while True: 
            
            # Change the nonce and recalculate the hash
            block.nonce = nonce
            block.hash = block.calculate_hash()
            # After updating the nonce
            
            # Print the hash being tried
            print(f"Nonce: {nonce}, Hash: {block.hash}")

            # Check if the hash meets the specified difficulty
            if block.hash.startswith(prefix):
                print(f"Proof of Work Successful! Nonce: {nonce}, Hash: {block.hash}")
                break

            nonce += 1

    def add_transaction(self, transaction):
        # Ensure that the transaction is valid before adding it to the blockchain
        if not isinstance(transaction, Transaction):
            raise ValueError("Invalid transaction. Must be an instance of the Transaction class.")

        if transaction.sender:
            if transaction.sender.balance < transaction.amount:
                raise ValueError("Insufficient funds for the transaction.")

            # Deduct the amount from the sender's balance
            transaction.sender.balance -= transaction.amount

        # Add the transaction to the list of current transactions
        self.current_transactions.append(transaction)

    def display_chain(self):
        for block in self.chain:
            formatted_timestamp = time.strftime("%m/%d/%Y %H:%M:%S", time.localtime(block.timestamp))
            transaction_ids = [transaction.transaction_id for transaction in block.transactions]
            print(f"Block #{block.block_number} | Hash: {block.hash}")
            print(f"Timestamp: {formatted_timestamp}")
            print(f"Transaction IDs: {transaction_ids}")
            print("--------------")

--------------
1. Transaction: Transfer 10 BTC from Alice to Bob
2. Transaction: Transfer 5 BTC from Bob to Charlie
3. Transaction: Transfer 8 BTC from Charlie to Alice
--------------

In [50]:
if __name__ == "__main__":
    # Create wallets
    alice_wallet = Wallet("Alice")
    bob_wallet = Wallet("Bob")
    charlie_wallet = Wallet("Charlie")
    miner_wallet = Wallet("Miner")

    # Initial balances
    alice_wallet.add_balance(100)
    bob_wallet.add_balance(50)
    charlie_wallet.add_balance(30)

# Display initial balances
alice_wallet.display_all_wallet()
bob_wallet.display_all_wallet()
charlie_wallet.display_all_wallet()

Wallet Alice:
  Public Key: 6f04bca22a151de4103aa78a645feb0eeed1eb0a12788de2d701be939f7ce25e
  Private Key: 71ca3849c2e6d70713137777a8e7440f934185ed698d77c674de5da8ce110922
  Balance: 100 units
Wallet Bob:
  Public Key: 49315ce157a885ec53058dc87ccbcfad3ed029961fee3824411eaee84c1aee6d
  Private Key: 4f2290ed5ded421d4eea00fda6a95b1448bb42a3c5476d53c0863306b47011da
  Balance: 50 units
Wallet Charlie:
  Public Key: 491f4f48e94e8949f6cdbe2f6c993dc9c136a4af37e9712038e2d540c67ee960
  Private Key: 204f0519c64174c8332ecdd787d79a68a1a8bbde24dc2497becfb7de32de8bda
  Balance: 30 units


In [51]:
# Create a blockchain
my_blockchain = Blockchain()

In [52]:
my_blockchain.display_chain() # Should only display the genesis block

Block #0 | Hash: bae22c192e2a6173f1fa5d85e6c5e611457337ec3f938f6fa3f31ab383a799ff
Timestamp: 12/05/2023 02:55:04
Transaction IDs: []
--------------


### Cria as transações e as executa (ainda não terminaram)

In [53]:
# Create transactions
transaction1 = Transaction(alice_wallet, bob_wallet, 10)
transaction2 = Transaction(bob_wallet, charlie_wallet, 5)
transaction3 = Transaction(charlie_wallet, alice_wallet, 8)

# Add transactions to the blockchain
my_blockchain.add_transaction(transaction1)
my_blockchain.add_transaction(transaction2)
my_blockchain.add_transaction(transaction3)

### Balanço Inicial das 3 Carteiras

In [54]:
alice_wallet.display_all_wallet()
bob_wallet.display_all_wallet()
charlie_wallet.display_all_wallet()

Wallet Alice:
  Public Key: 6f04bca22a151de4103aa78a645feb0eeed1eb0a12788de2d701be939f7ce25e
  Private Key: 71ca3849c2e6d70713137777a8e7440f934185ed698d77c674de5da8ce110922
  Balance: 90 units
Wallet Bob:
  Public Key: 49315ce157a885ec53058dc87ccbcfad3ed029961fee3824411eaee84c1aee6d
  Private Key: 4f2290ed5ded421d4eea00fda6a95b1448bb42a3c5476d53c0863306b47011da
  Balance: 45 units
Wallet Charlie:
  Public Key: 491f4f48e94e8949f6cdbe2f6c993dc9c136a4af37e9712038e2d540c67ee960
  Private Key: 204f0519c64174c8332ecdd787d79a68a1a8bbde24dc2497becfb7de32de8bda
  Balance: 22 units


### Publico Todos podem ver

In [55]:
transaction1.display_transaction()
transaction2.display_transaction()
transaction3.display_transaction()

Transaction:
  Sender Public Key: 6f04bca22a151de4103aa78a645feb0eeed1eb0a12788de2d701be939f7ce25e
  Recipient Public Key: 49315ce157a885ec53058dc87ccbcfad3ed029961fee3824411eaee84c1aee6d
  Amount: 10
  Timestamp: 12/05/2023 02:55:08
  Transaction ID: 8a210a02867a78081b508e16114ac9d53ff7d9df8cdb2a72570716714f7ed338
Transaction:
  Sender Public Key: 49315ce157a885ec53058dc87ccbcfad3ed029961fee3824411eaee84c1aee6d
  Recipient Public Key: 491f4f48e94e8949f6cdbe2f6c993dc9c136a4af37e9712038e2d540c67ee960
  Amount: 5
  Timestamp: 12/05/2023 02:55:08
  Transaction ID: f0f23d70270fcf754d069dcebc3671d8b4fcbf6c649932633d6283f3918cfe6f
Transaction:
  Sender Public Key: 491f4f48e94e8949f6cdbe2f6c993dc9c136a4af37e9712038e2d540c67ee960
  Recipient Public Key: 6f04bca22a151de4103aa78a645feb0eeed1eb0a12788de2d701be939f7ce25e
  Amount: 8
  Timestamp: 12/05/2023 02:55:08
  Transaction ID: d08f0115ae1f9784a1663154ce3761f2fc3b6be9bb998524a77d9cd86d5895e3


In [56]:
# Mine a block with a reward for the miner
miner_reward = 5
my_blockchain.mine_block(miner_wallet, miner_reward)

Nonce: 0, Hash: 54418b8da9dd504fc00586b3f0c671e7eab9ff0540146f4825dfcd3ebebb6772
Nonce: 1, Hash: a97453c204727e57f8f4ab270b06d697d8360286e1f00a2bf41264585d1f719d
Nonce: 2, Hash: 79b08605b79f74de949e4f3b7f9cf417b7f63f9dcea1ac25a56747c0bb927340
Nonce: 3, Hash: 7dc822f421b5ce6989d6250e2a0c60985355b045154dda18c0b73969f6d52c87
Nonce: 4, Hash: 99b76c7e9a743a2bc8bd84461343839cb2c71c201c7c311dd0313121e0681f08
Nonce: 5, Hash: 729dc1649d8ebce62f28858610d2f4227b378af0af7156d291d96406d9afa0ce
Nonce: 6, Hash: 2dccfef3d19b054ad5333baa35180a35d61d58168146b1511ac4f8bb3ed53e0f
Nonce: 7, Hash: 460be33b6f276b2bc3d9a1178df8772dc93773e5189b8474f9ce2ebd9ba6ff67
Nonce: 8, Hash: 3fd7ece4f02cee1dc76cf49dbbc5c550e36493716d57d3a7954f2e1f064555be
Nonce: 9, Hash: f7857f388567e823f477d3cc382309381eb359dd66e0769c69b7828479d96a3a
Nonce: 10, Hash: b1c58b1087de7e82292eaec7e1616346f4785e49ed5e8d821fcc9c59046bf81a
Nonce: 11, Hash: 0c872efea6d6af59e13446f1516d6d9d47d9a310b168cdfe423bd1236d929e82
Nonce: 12, Hash: b32077c8e

Bloco Minerado Diff4: Proof of Work Successful! Nonce: 61018, Hash: 0000d7da9481ae954607a4aec923b5054e7e053710b42eb5399ab597e1ebfe06

In [57]:
# Display the blockchain
my_blockchain.display_chain()

Block #0 | Hash: bae22c192e2a6173f1fa5d85e6c5e611457337ec3f938f6fa3f31ab383a799ff
Timestamp: 12/05/2023 02:55:04
Transaction IDs: []
--------------
Block #1 | Hash: 0000d7da9481ae954607a4aec923b5054e7e053710b42eb5399ab597e1ebfe06
Timestamp: 12/05/2023 02:55:38
Transaction IDs: ['8a210a02867a78081b508e16114ac9d53ff7d9df8cdb2a72570716714f7ed338', 'f0f23d70270fcf754d069dcebc3671d8b4fcbf6c649932633d6283f3918cfe6f', 'd08f0115ae1f9784a1663154ce3761f2fc3b6be9bb998524a77d9cd86d5895e3']
--------------


### Recomepensa do Miner

In [58]:
miner_wallet.display_all_wallet()

Wallet Miner:
  Public Key: bb5e3bb0d05bd32916c6af06fee616774c6c04d9b111a93592219465b1dc7308
  Private Key: 004580f24bcccaab029ad49276acf94f982455827c71908fb9c8c84aae678e89
  Balance: 5 units


### Resultado após Finalização das Transações

In [59]:
alice_wallet.display_all_wallet()
bob_wallet.display_all_wallet()
charlie_wallet.display_all_wallet()

Wallet Alice:
  Public Key: 6f04bca22a151de4103aa78a645feb0eeed1eb0a12788de2d701be939f7ce25e
  Private Key: 71ca3849c2e6d70713137777a8e7440f934185ed698d77c674de5da8ce110922
  Balance: 98 units
Wallet Bob:
  Public Key: 49315ce157a885ec53058dc87ccbcfad3ed029961fee3824411eaee84c1aee6d
  Private Key: 4f2290ed5ded421d4eea00fda6a95b1448bb42a3c5476d53c0863306b47011da
  Balance: 55 units
Wallet Charlie:
  Public Key: 491f4f48e94e8949f6cdbe2f6c993dc9c136a4af37e9712038e2d540c67ee960
  Private Key: 204f0519c64174c8332ecdd787d79a68a1a8bbde24dc2497becfb7de32de8bda
  Balance: 27 units
